<a href="https://colab.research.google.com/github/YogoBog/MemoryGameApp/blob/master/Guinness_search_engine.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b>בניית מנוע חיפוש מעל מאגר של שיאי גינס
</b></font>


https://drive.google.com/file/d/1GOxm-D9IUgsJwTJ0ZPEY6MEidpKJIW-D/view?usp=sharing הקובץ ממנו נלקחו הנתונים

In [ ]:
!unzip guinnessWorldRecords.zip

Archive:  guinnessWorldRecords.zip
replace guinnessWorldRecords/record_0.txt? [y]es, [n]o, [A]ll, [N]one, [r]ename: 

In [ ]:
from os import listdir
from os.path import isfile, join, isdir
mypath = "guinnessWorldRecords"

def get_all_files(mypath):
  filenames = []
  for f in listdir(mypath):
      filenames += [join(mypath, f)]
  return filenames

list_files = get_all_files(mypath)
list_files[:3]

['guinnessWorldRecords/record_908.txt',
 'guinnessWorldRecords/record_506.txt',
 'guinnessWorldRecords/record_1702.txt']

In [ ]:
import os
def load_data(mypath):
  texts = []
  for filename in os.listdir(mypath):
    if filename.endswith('.txt'):
      with open(os.path.join(mypath, filename), 'r') as f:
        text = f.read()
        texts.append(text)
  return texts


In [ ]:
docs = load_data("guinnessWorldRecords")
docs

In [ ]:
print(len(docs))

1971


<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b>שלב 01 - הכנת המידע</b></font></div>


### <div dir="rtl"><font color='#6400E4'><b>עיבוד הטקסט</b></font></div>


In [ ]:
import string
import nltk
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from nltk.tokenize import SpaceTokenizer
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('omw-1.4')

def preprocess_text(text):
  # Lowercase the text
  text = text.lower()
  # Remove punctuation
  text = text.translate(str.maketrans('', '', string.punctuation))
  # Split the text into tokens
  tokenizer = SpaceTokenizer()
  tokens = tokenizer.tokenize(text)
  # Remove stop words
  stop_words = set(stopwords.words('english'))
  filtered_tokens = [token for token in tokens if token.lower() not in stop_words]
  # Remove stemming
  ps = PorterStemmer()
  ps_tokens = [ps.stem(word) for word in filtered_tokens]
  # Remove lemmatization
  lem = WordNetLemmatizer()
  lem_tokens = [lem.lemmatize(word) for word in ps_tokens]
  return lem_tokens

preprocess_text("The BOYS are jumping on the trampoline.") # need to return ['boy', 'jump', 'trampolin']

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


['boy', 'jump', 'trampolin']

In [ ]:
def preprocess_docs(docs):
  tokenized_docs = []
  for doc in docs:
    tokens = preprocess_text(doc)
    tokenized_docs.append(tokens)
  return tokenized_docs

<h1 dir="rtl">

**קראו לפונקציה preprocess_docs והחזירו את רשימת המסמכים לאחר עיבוד וחלוקה לטוקנים.**


In [ ]:
# Running this function takes some time.
list_of_tokens_docs = preprocess_docs(docs)
list_of_tokens_docs

[['sword',
  'swallow',
  'simultan',
  'femal',
  '⚔️',
  'day',
  '2004',
  'natasha',
  'verushka',
  'usa',
  'swallow',
  '13',
  'sword',
  'least',
  '381',
  'cm',
  '15',
  'long',
  '3rd',
  'annual',
  'side',
  'show',
  'gather',
  'sword',
  'swallow',
  'convent',
  'wilkesbarr',
  'pennsylvania',
  'usa',
  '',
  '',
  '',
  'swordswallow',
  'sword',
  'sideshow',
  'guinnessworldrecord',
  'officiallyamaz',
  'perform',
  'perform',
  'pennsylvania',
  'httpswwwinstagramcompbnrhgpdnzdt'],
 ['know',
  'day',
  'isso',
  'maythe4th',
  '\u2063',
  '\u2063',
  'special',
  'starwar',
  'theme',
  'day',
  'show',
  'coolest',
  'object',
  'record',
  'holder',
  'steve',
  'sansweet',
  '',
  'superfan',
  'titl',
  'world',
  'largest',
  'collect',
  'star',
  'war',
  'memorabilia',
  '\u2063',
  '\u2063',
  'journalist',
  'author',
  'presid',
  'ranchoobiwan',
  'nonprofit',
  'museum',
  'petaluma',
  'california',
  'steve',
  'place',
  'hous',
  'collect',
  '

<div dir=rtl align=right>

### <div dir="rtl"><font color='#6400E4'><b>חישוב מילוני tf-idf לכל מסמך</b></font></div>


In [ ]:
import math

# Calculate the term frequency (TF) score for a given token in a tokenized document.
def calc_tf(token, tokens_of_document):
  return tokens_of_document.count(token)/len(tokens_of_document)

# Calculate the inverse document frequency (IDF) score for a given token in a list of tokenized documents.
def calc_idf(token, list_of_tokens_docs):
  freq_token = 0
  for tokens_doc in list_of_tokens_docs:
    if token in tokens_doc:
      freq_token += 1
  return math.log10(len(list_of_tokens_docs)/freq_token)

# Calculate the term frequency-inverse document frequency (TF-IDF) score for a given token in a tokenized document.
def calc_tf_idf(token, tokens_doc, list_of_tokens_docs):
  return calc_tf(token, tokens_doc) * calc_idf(token, list_of_tokens_docs)

# Calculate the term frequency-inverse document frequency (TF-IDF) scores for all tokens in a tokenized document, and store it on dictionary.
def calc_tf_idf_doc(tokens_doc, list_of_tokens_docs):
  tf_idf_doc = {}
  for token in tokens_doc:
    score = calc_tf_idf(token, tokens_doc, list_of_tokens_docs)
    tf_idf_doc[token] = score
  return tf_idf_doc

# Calculate the term frequency-inverse document frequency (TF-IDF) scores for all tokens in a list of tokenized documents.
# The function then appends the dictionary of TF-IDF scores to the all_docs_tf_idf list.
# The function returns the all_docs_tf_idf list, which contains the TF-IDF scores dictionary for all tokens in all documents.
# The list of TF-IDF dictionaries preserves the order of the documents. The first dictionary in the result list corresponds to the first document in the list that was entered.
def calc_tf_idf_all_docs(list_of_tokens_docs):
  tf_idf_docs = []
  for tokens_doc in list_of_tokens_docs:
    tf_idf_docs += [calc_tf_idf_doc(tokens_doc, list_of_tokens_docs)]
  return tf_idf_docs

In [ ]:
# load data to list of tf-idf dictionary.
# Running this function takes long time. (2 min).
tf_idf_docs = calc_tf_idf_all_docs(list_of_tokens_docs)
tf_idf_docs

[{'sword': 0.21275544116805917,
  'swallow': 0.1792381890925746,
  'simultan': 0.0439835348889066,
  'femal': 0.030960506317431052,
  '⚔️': 0.06872110657462879,
  'day': 0.01676174636743353,
  '2004': 0.048625771429645415,
  'natasha': 0.08035821034827911,
  'verushka': 0.08035821034827911,
  'usa': 0.0357265248694131,
  '13': 0.03830270133362571,
  'least': 0.05167305768838444,
  '381': 0.07301601533208445,
  'cm': 0.026599186381061426,
  '15': 0.0364718554835576,
  'long': 0.030005576464695725,
  '3rd': 0.07301601533208445,
  'annual': 0.0433212849854038,
  'side': 0.04714533629906952,
  'show': 0.024558168154858957,
  'gather': 0.040273998726664775,
  'convent': 0.06567382031588978,
  'wilkesbarr': 0.08035821034827911,
  'pennsylvania': 0.13134764063177956,
  '': 0.003924766361546253,
  'swordswallow': 0.06872110657462879,
  'sideshow': 0.06567382031588978,
  'guinnessworldrecord': 0.0007342657327162384,
  'officiallyamaz': 0.004408372487136743,
  'perform': 0.06610572544686949,
  '

<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b> שלב 02 - שאילתת המשתמש

</b></font>


In [ ]:
def preprocess_user_query(query):
  return preprocess_text(query)

preprocess_user_query("Who is the tallest DOG in the world?") # need to return ["tallest", "dog", "world"]

['tallest', 'dog', 'world']

<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b> שלב 03 - חישוב ציוני המסמכים



In [ ]:
def calc_score_doc(tf_idf_doc, query_tokens):
  score = 0
  for token in query_tokens:
    if token in tf_idf_doc:
      score += tf_idf_doc[token]
  return score


In [ ]:
def calc_scores_docs(tf_idf_docs, query_tokens):
  scores = []
  for tf_idf_doc in tf_idf_docs:
    score = calc_score_doc(tf_idf_doc, query_tokens)
    scores.append(score)
  return scores

<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b> שלב 04 - דירוג המסמכים


In [ ]:
def rank_docs(docs, scores_docs):
  doc_score_pairs = list(zip(docs, scores_docs))
  sorted_pairs = sorted(doc_score_pairs, key=lambda x: x[1], reverse=True)
  top_docs = sorted_pairs[:5]
  ranked_docs = [doc_score_pair[0] for doc_score_pair in top_docs]
  return ranked_docs


<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b> איחוד שלבי החיפוש:
</b></font>




In [ ]:
def search(search_question, tf_idf_per_doc, docs):
  sc = preprocess_user_query(search_question)
  csd = calc_scores_docs(tf_idf_per_doc,sc)
  return rank_docs(docs,csd)


search("Who is the tallest DOG in the world?", tf_idf_docs, docs)

['Tallest dog living (male) 🐕 Zeus - 1.046 metres (3 ft 5.18 in) 🇺🇸  #dog #dogs #greatdane #tallest #tall #petstagram #guinnessworldrecords #officiallyamazing https://www.instagram.com/p/CdLmYkaDiA_',
 'Longest ears on a living dog 🐶 68 cm (26.77 in) - Lou and owner Paige Olsen 🇺🇸  #dog #ears #dogs #coonhound #guinnessworldrecords #officiallyamazing https://www.instagram.com/p/CdZR_zVI7Sw',
 "Meet Freddy the Great Dane who this week was revealed to be our new record holder for 'Tallest dog living'. His height is an incredible 1.035 metres (3 ft 4.75 in) from foot to withers. @freddygreatdane lives in Leigh-on-Sea, UK with owner Claire Stoneman and featured in the @channel5_tv show 'Biggest Dog In The World' 🐕  #dogs #pets #dog #greatdane #guinnessworldrecords #officiallyamazing https://www.instagram.com/p/BOvcgIlg1TP",
 'Most cartwheels weaved through by a dog in one minute - 22 by Nala and Frederike Spyrka 🇩🇪🐶  #cartwheels #dogs #officiallyamazing #guinnessworldrecords https://www.ins

<div dir=rtl align=right>

<div dir=rtl align=right>

# <div dir="rtl"><font color='#6400E4'><b> הוספת ממשק חיפוש


In [ ]:
#@title Magshimim AI Searcher:
search_question = "" #@param {type:"string"}
search(search_question, tf_idf_docs, docs)

['Throwback Thursday: Longest Marathon on a Roller Coaster  In 2007 school teacher and roller coaster superfan Richard Rodriguez (USA) rode the Pepsi Max Big One and Big Dipper roller coasters at Blackpool Pleasure Beach (UK) for 405 hours 40 minutes from 27 July to 13 August. Richard ate, drank and slept on the coasters and donated funds raised through the record attempt to diabetes research. His record has yet to be beaten. Will you be the next challenger?  #guinnessworldrecords #officiallyamazing #rollercoaster #endurance #worldrecord #blackpool #tbt #throwbackthursday https://www.instagram.com/p/BGKyx9tRHeA',
 'Most swords swallowed simultaneously by a female ⚔️ On this day in 2004, Natasha Verushka (USA) swallowed 13 swords, each at least 38.1 cm (15 in) long at 3rd Annual Side Show Gathering and Sword Swallowers Convention, Wilkes-Barre, Pennsylvania, USA.  ______________________________________________________  #swordswallower #swords #sideshow #guinnessworldrecords #officiallya